In [ ]:
# FIR Filter anlegen

from scipy import signal
from scipy.fft import fft, fftfreq
import numpy as np
import matplotlib.pyplot as plt
from ipywidgets import interact


def fir_filter(taps, input):                    # taps, input sind 1d Eingabelisten mit Koeffizienten und Samples
    fir=[]                                      # Ausgabeliste anlegen
    for j in range(0, len(input) - len(taps)):  # Erste Samples (Koeffizientenzahl) zählen nicht zur Filterantwort
        fir_i=0
        for i in range (len(taps)):             # Durch Koeffizienten durchiterieren
            taps_i = taps[i]                    # taps_i ist Laufvariable
            fir_i += taps_i*input[j+i]          # fir_i ist Laufvariable für Filterergebnis - jeweiliger Koeffizient wird mit dem i-ten Input-Sample der reduzierten Liste j multipliziert
        fir.append(fir_i)                       # hänge Ergebnis an Ergebnisliste an
    return fir


[0, 0, 0, 0, 0, 0, 0, 0, 0]


[0, 0, 0, 0, 0, 0, 0, 0, 0]

In [ ]:
# Chirp Generator

n=3000 # number of samples to use for the chirp
fs=20000 # The sampling rate for the chrip
f0=100# the start frequency in Hz for the chirp
f1=1000 # the stop frequency of the chirp
t1=n/fs # the total length of the chirp in s

t_chrip = np.linspace(0, t1, n)
# generate a chrip and scale to int16 (1 bit for sign)
y_chrip = np.round(signal.chirp(t_chrip, f0=f0, f1=f1, t1=t1, method='linear')*(2**15-1)).astype(int)
cutsamps = 45
y_chrip = y_chrip[cutsamps:]
t_chrip = t_chrip[cutsamps:]

# Generate an array were the data is present in an interleaved format with the inverted signal 
y_chrip_interleaved = np.empty((2*y_chrip.size), dtype=y_chrip.dtype)pa
y_chrip_interleaved[0::2] = y_chrip
y_chrip_interleaved[1::2] = -1*y_chrip[::-1]

file_str= f"#define CHIRP_DATA_SAMPLE_RATE {int(fs)}\n"\
          "#define CHIRP_DATA_LEN"f" {y_chrip.size}" "\n"\
          "#define CHIRP_DATA_INTERLEAVED_LEN"f" {y_chrip_interleaved.size}" "\n"\
          "#define CHIRP_DATA {" + ",".join(y_chrip.astype(str)) +"}\n"\
          "#define CHIRP_DATA_INTERLEAVED_INVERTED {" + ",".join(y_chrip_interleaved.astype(str)) +"}" "\n"

with open("pcm_chirp/include/chirp_data.h", "w") as f:
    f.write(file_str)